<div class="alert alert-block alert-success">
<b>Comentario general del revisor</b> <a class="tocSkip"></a><br />
Status del proyecto: <b>Aprobado</b>
</div>


¡Hola!<br />
Soy **Francisco Cortés**, estoy contento de revisar tu proyecto y ser parte de tu proceso de aprendizaje.
A lo largo del texto, haré algunas observaciones sobre mejoras en el código y también haré comentarios sobre tus percepciones sobre el tema. Si existe algún error en el código, no te preocupes, estoy aquí para ayudarte a mejorarlo, en la primera iteración te lo señalaré para que tengas la oportunidad de corregirlo, pero si aún no encuentras una solución para esta tarea, te daré una pista más precisa en la próxima iteración y también algunos ejemplos prácticos. Estaré abierto a retroalimentación y discusiones sobre el tema.<br />
Encontrarás mis comentarios a continuación - **por favor no los muevas, modifiques o borres**.
Revisaré cuidadosamente tu código para comprobar que se han cumplido con los requisitos y te proporcionaré mis comentarios en cajas verdes, amarillas o rojas como esta:

<div class="alert alert-block alert-success">
<b>Comentario del revisor</b> <a class="tocSkip"></a>

Si la ejecución fue perfecta succesfully.
</div>

<div class="alert alert-block alert-warning">
<b>Comentario del revisor</b> <a class="tocSkip"></a>

Si existe alguna recomendación para que tu código mejore.
</div>

<div class="alert alert-block alert-danger">

<b>Comentario del revisor</b> <a class="tocSkip"></a>

Si existen correcciones necesarias para cumplir con los requisitos. El trabajo no puede ser aceptado si hay alguna caja roja.
</div>

Puedes responderme de la siguiente manera:

<div class="alert alert-block alert-info">
<b>Respuesta del estudiante.</b> <a class="tocSkip"></a>
</div>

# **Project 11**

**Librerías**

In [7]:
# Importo todas las librerías que me serán de utilidad a lo largo del proyecto.

import pandas as pd
import numpy as np
import scipy.stats as stats
from scipy.stats import chi2_contingency
from scipy.stats import ttest_ind
import math as mth
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px


## **Paso 1: Leer el archivo de datos**

**Preparación de los datos: Dataframes (df)**

In [8]:
# Leo los archivos csv, los convierto en dataframes y me familiarizo con los datos que contienen.

#data = pd.read_csv('Datasets/logs_exp_us.csv', sep='\t')
data = pd.read_csv('./datasets/logs_exp_us.csv', sep='\t')
data.sample(5)

EventName         DeviceIDHash  EventTimestamp  ExpId
185396  MainScreenAppear  1529531054838639703      1565079209    247
67025   MainScreenAppear  5530821733261873312      1564765553    248
9388    MainScreenAppear  6404569898667835532      1564646410    247
13991   MainScreenAppear  1640129893004506946      1564654756    247
110443  MainScreenAppear  6463833207814436303      1564897383    247

<div class="alert alert-block alert-success"> <b>Comentario del revisor</b> <a class="tocSkip"></a><br>

Correcto!<br/>

Buena manera de leer los datos utilizando el separador correcto.
</div>

## **Paso 2: Preparar los datos para el análisis**

In [9]:
# Cambio el nombre de las columnas por otros que me sean más fácil de comprender
data.columns = ['event', 'device_id', 'time_stamp', 'group']
data.sample(5)

event            device_id  time_stamp  group
64695          CartScreenAppear  3921210056250168865  1564761825    246
233401  PaymentScreenSuccessful  3337471580007169353  1565190762    246
30135        OffersScreenAppear  4148267947677649217  1564678357    248
99438          MainScreenAppear  6979088364342662031  1564848669    247
198010         MainScreenAppear  7235587238353002284  1565101303    248

In [10]:
# Reviso los tipos de las columnas y los cambio como convengan
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 244126 entries, 0 to 244125
Data columns (total 4 columns):
 #   Column      Non-Null Count   Dtype 
---  ------      --------------   ----- 
 0   event       244126 non-null  object
 1   device_id   244126 non-null  int64 
 2   time_stamp  244126 non-null  int64 
 3   group       244126 non-null  int64 
dtypes: int64(3), object(1)
memory usage: 7.5+ MB


**Transformación de valores**

In [11]:
# Modifico el contenido de las columnas para comprenderlo más fácilmente

data['date_time'] = pd.to_datetime(data['time_stamp'], unit='s')
data['date'] = data['date_time'].dt.date

# Separo las palabras de event usando expresiones regulares
data['event'] = data['event'].str.replace(r'(?<!^)(?=[A-Z])', ' ', regex=True)

# Reemplazo valores numéricos por cadenas de texto
data['group'] = data['group'].replace({246: 'A1', 247: 'A2', 248: 'B'})
data

event            device_id  time_stamp group  \
0              Main Screen Appear  4575588528974610257  1564029816    A1   
1              Main Screen Appear  7416695313311560658  1564053102    A1   
2       Payment Screen Successful  3518123091307005509  1564054127     B   
3              Cart Screen Appear  3518123091307005509  1564054127     B   
4       Payment Screen Successful  6217807653094995999  1564055322     B   
...                           ...                  ...         ...   ...   
244121         Main Screen Appear  4599628364049201812  1565212345    A2   
244122         Main Screen Appear  5849806612437486590  1565212439    A1   
244123         Main Screen Appear  5746969938801999050  1565212483    A1   
244124         Main Screen Appear  5746969938801999050  1565212498    A1   
244125       Offers Screen Appear  5746969938801999050  1565212517    A1   

                 date_time        date  
0      2019-07-25 04:43:36  2019-07-25  
1      2019-07-25 11:11:42  2019-07-25  
2      2019-07-25 11:28:47  2019-07-25  
3      2019-07-25 11:28:47  2019-07-25  
4      2019-07-25 11:48:42  2019-07-25  
...                    ...         ...  
244121 2019-08-07 21:12:25  2019-08-07  
244122 2019-08-07 21:13:59  2019-08-07  
244123 2019-08-07 21:14:43  2019-08-07  
244124 2019-08-07 21:14:58  2019-08-07  
244125 2019-08-07 21:15:17  2019-08-07  

[244126 rows x 6 columns]

In [12]:
# Las columnas han cambiado a los tipos adecuados y los valores que contienen han sido transformados de manera que me son convenientes.
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 244126 entries, 0 to 244125
Data columns (total 6 columns):
 #   Column      Non-Null Count   Dtype         
---  ------      --------------   -----         
 0   event       244126 non-null  object        
 1   device_id   244126 non-null  int64         
 2   time_stamp  244126 non-null  int64         
 3   group       244126 non-null  object        
 4   date_time   244126 non-null  datetime64[ns]
 5   date        244126 non-null  object        
dtypes: datetime64[ns](1), int64(2), object(3)
memory usage: 11.2+ MB


**Data cleaning: duplicates and missing data**

In [13]:
#Busco duplicados y valores perdidos en el df data

def duplicates_and_nulls(df):
    if df.duplicated().sum() == 0:
        print('No se encontraron filas duplicadas en este dataframe')
        
    else:
        print(f'hay {df.duplicated().sum()} valores duplicados')

    if df.isna().sum().sum() == 0:
        print('No se encontraron valores perdidos en este dataframe')
    else:
        print(f"Hay {df.isna().sum().sum()} valores perdidos en este dataframe")


duplicates_and_nulls(data)

hay 413 valores duplicados
No se encontraron valores perdidos en este dataframe


In [14]:
# Se encontraron 413 valores duplicados, procedo a eliminarlos
data = data.drop_duplicates()

In [15]:
print(f'Hay {data.duplicated().sum()} duplicados en data')

Hay 0 duplicados en data


<div class="alert alert-block alert-success"> <b>Comentario del revisor</b> <a class="tocSkip"></a><br>

Correcto!<br/>

Buena manera de encontrar y eliminar los duplicados además de hacer un cambio a los tipos de datos de las columnas y renombrarlas.
</div>

## **Paso 3. Estudiar y comprobar los datos**

**¿Cuántos eventos hay en los registros?**

En total tenemos 243713 eventos realizados, los cuales se dividen en 'Main Screen Appear', 'Payment Screen Successful', 'Cart Screen Appear', 'Offers Screen Appear' y 'Tutorial'.

In [16]:
# Aquí puedo observar cuantos eventos tenemos de cada uno
data['event'].value_counts()

event
Main Screen Appear           119101
Offers Screen Appear          46808
Cart Screen Appear            42668
Payment Screen Successful     34118
Tutorial                       1018
Name: count, dtype: int64

**¿Cuántos usuarios y usuarias hay en los registros?**

In [17]:
#print(f'Contamos con {data['device_id'].nunique()} diferentes dispositivos, cada uno representa a un usuario distinto.')
print(f"Contamos con {data['device_id'].nunique()} diferentes dispositivos, cada uno representa a un usuario distinto.")


Contamos con 7551 diferentes dispositivos, cada uno representa a un usuario distinto.


**¿Cuál es el promedio de eventos por usuario?**

In [18]:
events_by_user = data.groupby('device_id')['event'].count().reset_index()
#print(f'El promedio de eventos por usuario es {events_by_user['event'].mean().round(2)}')
print(f"El promedio de eventos por usuario es {events_by_user['event'].mean().round(2)}")

El promedio de eventos por usuario es 32.28


In [19]:
mode = events_by_user['event'].mode()

In [20]:
# Histograma de la ditribución de los eventos por usuario

fig = px.histogram(
    events_by_user, x='event', title=f'La mayoría de nuestros usuarios cuenta con 5 eventos', range_x=[1, 100]
)

fig.update_layout(
    xaxis_title="Número de eventos por usuario", 
    yaxis_title="Cantidad de usuarios",
)

fig.show()

El promedio de eventos por usuario es 32 sin embargo la mayoría de nuestros usuarios tienen entre 5 y 9 eventos.

**¿Qué periodo de tiempo cubren los datos?**

In [21]:
# Encuentro la fecha más antigua y la más reciente de nuestros datos
print(f"La fecha más antigua de nuestros datos es {data['date'].min()} \nLa fecha más reciente de nuestros datos es {data['date'].max()}")

La fecha más antigua de nuestros datos es 2019-07-25 
La fecha más reciente de nuestros datos es 2019-08-07


In [22]:
# Reviso cuantos eventos tengo en cada día.
data['date'].value_counts().reset_index().sort_values(by='date')

date  count
13  2019-07-25      9
12  2019-07-26     31
11  2019-07-27     55
10  2019-07-28    105
9   2019-07-29    184
8   2019-07-30    412
7   2019-07-31   2030
0   2019-08-01  36141
3   2019-08-02  35554
4   2019-08-03  33282
5   2019-08-04  32968
1   2019-08-05  36058
2   2019-08-06  35788
6   2019-08-07  31096

In [23]:
# Creo un histograma que muestre cuantos registros por fecha tengo en mi dataframe

fig = px.histogram(
    data, x='date', title='Eventos por fecha',
)

fig.update_layout(
    xaxis_title="Número de eventos por usuario", 
    yaxis_title="Count",
)

fig.show()

Al parecer no tenemos los datos completos del mes de julio, a partir del 1ero de agosto ya tenemos suficientes datos para hacer un análisis, es por ello que ignoraré los datos de julio y me concentraré en la primera semana de agosto (del 1ero al 7 de agosto).

<div class="alert alert-block alert-success"> <b>Comentario del revisor</b> <a class="tocSkip"></a><br>

Bien hecho!<br/>

La manera en que se muestran los datos en el histograma es correcta.
</div>

**Filtrado de datos**

In [24]:
# Filtro los datos al mes de agosto
df_agosto = data[data['date_time'].between('2019-08-01', '2019-08-31')]

<div class="alert alert-block alert-success"> <b>Comentario del revisor</b> <a class="tocSkip"></a><br>

Correcto!<br/>

Buena manera de obtener unicamente los datos que nos son relevantes basando tu decisión en los datos encontrados
</div>

In [25]:
# Agrupo por grupo para identificar que haya usuarios de los 3 grupos.
df_agosto.groupby('group')['device_id'].nunique().reset_index()

group  device_id
0    A1       2484
1    A2       2513
2     B       2537

<div class="alert alert-block alert-success">
<b>Comentario de Revisor</b> <a class="tocSkip"></a><br/>

Correcto!<br/>    
Buena manera de ordenar los datos, se puede ver que los grupos son bastante similares en tamaño

</div>

## **Paso 4. Estudiar el embudo de eventos**

In [26]:
df_agosto['event'].value_counts()

event
Main Screen Appear           117328
Offers Screen Appear          46333
Cart Screen Appear            42303
Payment Screen Successful     33918
Tutorial                       1005
Name: count, dtype: int64

In [27]:
# Eventos en los registros y su frecuencia

#values = df_agosto['event'].value_counts().reset_index().sort_values(by='count', ascending=False)
values = df_agosto['event'].value_counts().reset_index().sort_values(by='event', ascending=False)
values.columns = ['event', 'frecuency']
values

event  frecuency
4                   Tutorial       1005
3  Payment Screen Successful      33918
1       Offers Screen Appear      46333
0         Main Screen Appear     117328
2         Cart Screen Appear      42303

In [28]:
# Muestro en una gráfica la frecuencia 

fig = px.bar(
    values, x='event', y='frecuency', title='Aparecer en la página principal es el evento más recurrente'
)

fig.update_layout(
    xaxis_title="Eventos", 
    yaxis_title=" ",
)

fig.show()

<div class="alert alert-block alert-success">
<b>Comentario de Revisor</b> <a class="tocSkip"></a>

Correcto!<br/>
Buena manera de mostrar el resultado, se puede observar claramente la perdida de usuarios en cada una de las etapas

</div>

Evidentemente entrar a la página principal es el evento más recurrente, debido a que todos los usuarios deben pasar por ahí cuando acceden.

In [29]:
# Busco cuantos usuarios unicos realizaron cada uno de los eventos y la proporción de los usuarios totales que realizaron este evento

events = df_agosto.groupby('event').agg({'device_id': 'nunique'}).reset_index()
events['proportion%'] = ((events['device_id'] / df_agosto['device_id'].nunique()) * 100).round(2)
proportions = events.sort_values(by='proportion%', ascending=False).reset_index()

Aquí podemos observar el orden en el que ocurren los eventos, es una secuencia que comienza por acceder a la página principal, luego pasar a la página de ofertas y posteriormente la pantalla del carrito de compras para concluir con la pantalla de pago, así se ve el embudo por el que pasan nuestros clientes. Por otra parte el tutorial parece no ser visto por muchos usuarios, no me es posible determinar en qué momento deciden ver el tutorial los usuarios.

Le secuencia es la siguiente:

1. Main Screen Appear 
2. Offers Screen Appear
3. Cart Screen Appear
4. Payment Screen Successful	


In [30]:
# Creo la proporción relativa

proportions['relative_proportion%'] = proportions['device_id'] / proportions['device_id'].shift(1) * 100
proportions.loc[0, 'relative_proportion%'] = 100
proportions


index                      event  device_id  proportion%  \
0      1         Main Screen Appear       7419        98.47   
1      2       Offers Screen Appear       4593        60.96   
2      0         Cart Screen Appear       3734        49.56   
3      3  Payment Screen Successful       3539        46.97   
4      4                   Tutorial        840        11.15   

   relative_proportion%  
0            100.000000  
1             61.908613  
2             81.297627  
3             94.777718  
4             23.735519

In [31]:
# Crear gráfico de embudo con los porcentajes relativos
fig = px.funnel(
    proportions, 
    x='proportion%',  # Proporción relativa en el eje X
    y='event',                 # Eventos en el eje Y
    title="En el evento 'Offers Screen Appear' perdemos la mayor proporción de usuarios",
    labels={'relative_proportion%': 'Proporción Relativa (%)', 'event': 'Evento'},
    width=800, 
    height=600
)

fig.show()

Al pasar de 'Main Screen Appear' a 'Offers Screen Appear' es el momento en donde en proporción se pierden más clientes, de todos los usuarios que llegan al Main Screen, menos del 62 % pasan a Offers Screen; los demás pasos tienen una mejor retención, el 81% de los usuarios que pasaron al segundo paso llegan al tercero (Cart Screen) y de los usuarios que llegan al tercero casi el 95% de ellos termina la compra.

<div class="alert alert-block alert-success">
<b>Comentario de Revisor</b> <a class="tocSkip"></a>

Bien hecho!<br/>

Me parece una forma muy acertada d emostrar la información del embudo, cada una de las etapas esta claramente plasmada

</div>

**¿Qué proporción de los clientes realiza todo el embudo?**

In [32]:
df = df_agosto[df_agosto['event'] != 'Tutorial']

In [33]:
# Agrupo el df por device_id para encontrar a los usuarios que tienen los 4 eventos
grouped = df.groupby('device_id')['event'].nunique().reset_index()
full_funnel = grouped[grouped['event'] == 4]
full_funnel.info()

<class 'pandas.core.frame.DataFrame'>
Index: 3429 entries, 1 to 7526
Data columns (total 2 columns):
 #   Column     Non-Null Count  Dtype
---  ------     --------------  -----
 0   device_id  3429 non-null   int64
 1   event      3429 non-null   int64
dtypes: int64(2)
memory usage: 80.4 KB


Existen 3429 incidencias donde un usuario realizó exitosamente todo el recorrido por el embudo.

In [34]:
print(f"{full_funnel['device_id'].nunique()} usuarios únicos han recorrido por completo el embudo al menos una vez.")

3429 usuarios únicos han recorrido por completo el embudo al menos una vez.


**Porcentaje de usuarios y usuarias que hace todo el viaje desde su primer evento hasta el pago**

In [35]:
# Encuentro el total de usuarios que pasaron el embudo por completo, y después lo divido entre el total de usuarios para obtener la proporción.

total_users = df_agosto['device_id'].nunique()
total_funnel = full_funnel['device_id'].nunique()

proportion_of_users = round((total_funnel / total_users ) * 100, 2)

print(f"El {proportion_of_users}% de nuestros usuarios concluyó todo el embudo.")

El 45.51% de nuestros usuarios concluyó todo el embudo.


## **Paso 5. Estudiar los resultados del experimento**



**¿Cuántos usuarios y usuarias hay en cada grupo?**

In [36]:
# Usuarios agrupados por grupo de experimento
df_agosto.groupby('group')['device_id'].nunique().reset_index()

group  device_id
0    A1       2484
1    A2       2513
2     B       2537

Tenemos 2484 usuarios en A1 (muestra 246), 2513 usuarios en A2 (muestra 247), y el grupo B contamos con 2537 usuarios.

In [37]:
# Me aseguro de que estos grupos no sean muy distintos

# Datos de los grupos
A1 = 2484
A2 = 2513
B = 2537

# Diferencia porcentual entre el grupo más grande y el más pequeño

diff_percentage1 = ((A2 - A1) / A2) * 100
diff_percentage2 = ((B - A1) / B) * 100


print(f"La diferencia porcentual entre A2 y A1 es del {diff_percentage1:.2f}%")
print(f"La diferencia porcentual entre B y A1 es del {diff_percentage2:.2f}%")


La diferencia porcentual entre A2 y A1 es del 1.15%
La diferencia porcentual entre B y A1 es del 2.09%


**¿Existe una diferencia estadísticamente significativa entre las muestras?**

Los grupos A (246 y 247) son muy similares tan sólo hay una diferencia del 1.15%.

Entre el grupo más grande (B) y el grupo más pequeño (A1) existe tan solo una diferencia del 2%, por lo tanto es aceptable trabajar con estos datos; más de un 10% de diferencia sí sería algo significativo.

In [38]:
# Datos de ejemplo (número de usuarios en A1 y A2)

def sizes(group1, group2):

    # Tabla de frecuencias observadas
    observed = [group1, group2]
    expected = [sum(observed)/2, sum(observed)/2]

    # Prueba de chi-cuadrado
    chi2_stat, p_value = stats.chisquare(observed, expected)

    if p_value < 0.05:
        print("Existe una diferencia estadísticamente significativa (rechazamos H₀)")
    else:
        print("No hay diferencia significativa (no rechazamos H₀)")


In [39]:
# Comparación entre los grupos

print('Comparación entre A1 y A2:')
sizes(A1, A2)
print()
print('Comparación entre A1 y B:')
sizes(A1, B)
print()
print('Comparación entre A2 y B:')
sizes(A1, A2)

Comparación entre A1 y A2:
No hay diferencia significativa (no rechazamos H₀)

Comparación entre A1 y B:
No hay diferencia significativa (no rechazamos H₀)

Comparación entre A2 y B:
No hay diferencia significativa (no rechazamos H₀)


**Comparación de los grupos**

Comienzo separando el df por grupos y agrupándolos por eventos.

In [40]:
# Eventos del grupo A1

groupA1 = df_agosto[df_agosto['group'] == 'A1']
eventsA1 = groupA1.groupby('event')['device_id'].nunique().reset_index()
eventsA1.columns = ['event', 'users']

eventsA1['proportion'] = eventsA1['users'] / groupA1['device_id'].nunique()
print(f"El total de usuarios en el grupo A1 es de {groupA1['device_id'].nunique()}")
eventsA1.sort_values(by='users', ascending=False)

El total de usuarios en el grupo A1 es de 2484


event  users  proportion
1         Main Screen Appear   2450    0.986312
2       Offers Screen Appear   1542    0.620773
0         Cart Screen Appear   1266    0.509662
3  Payment Screen Successful   1200    0.483092
4                   Tutorial    278    0.111916

In [41]:
# Eventos del grupo A2

groupA2 = df_agosto[df_agosto['group'] == 'A2']
eventsA2 = groupA2.groupby('event')['device_id'].nunique().reset_index()
eventsA2.columns = ['event', 'users']
eventsA2['proportion'] = eventsA2['users'] / groupA2['device_id'].nunique()
print(f"El total de usuarios en el grupo A2 es de {groupA2['device_id'].nunique()}")
eventsA2.sort_values(by='users', ascending=False)

El total de usuarios en el grupo A2 es de 2513


event  users  proportion
1         Main Screen Appear   2476    0.985277
2       Offers Screen Appear   1520    0.604855
0         Cart Screen Appear   1238    0.492638
3  Payment Screen Successful   1158    0.460804
4                   Tutorial    283    0.112614

In [42]:
# Eventos del grupo B

groupB = df_agosto[df_agosto['group'] == 'B']
eventsB = groupB.groupby('event')['device_id'].nunique().reset_index()
eventsB.columns = ['event', 'users']
eventsB['proportion'] = eventsB['users'] / groupB['device_id'].nunique()

print(f"El total de usuarios en el grupo B es de {groupB['device_id'].nunique()}")
eventsB.sort_values(by='users', ascending=False)

El total de usuarios en el grupo B es de 2537


event  users  proportion
1         Main Screen Appear   2493    0.982657
2       Offers Screen Appear   1531    0.603469
0         Cart Screen Appear   1230    0.484825
3  Payment Screen Successful   1181    0.465510
4                   Tutorial    279    0.109972

Ahora veamos si hay diferencia estadísica entre estos valores.

In [43]:
# Combino los 3 df en uno solo para utilizarlo dentro de una función
table_proportions = eventsA1.merge(eventsA2, on="event", suffixes=('_A1', '_A2'))

table_proportions['users_A'] = table_proportions['users_A1'] + table_proportions['users_A2']
table_proportions['proportion_A'] = (eventsA1['users'] + eventsA2['users']) / (groupA1['device_id'].nunique() + groupA2['device_id'].nunique())

table_proportions = table_proportions.merge(eventsB, on="event")
table_proportions = table_proportions.rename(columns={'users': 'users_B', 'proportion': 'proportion_B'})
table_proportions

event  users_A1  proportion_A1  users_A2  \
0         Cart Screen Appear      1266       0.509662      1238   
1         Main Screen Appear      2450       0.986312      2476   
2       Offers Screen Appear      1542       0.620773      1520   
3  Payment Screen Successful      1200       0.483092      1158   
4                   Tutorial       278       0.111916       283   

   proportion_A2  users_A  proportion_A  users_B  proportion_B  
0       0.492638     2504      0.501101     1230      0.484825  
1       0.985277     4926      0.985791     2493      0.982657  
2       0.604855     3062      0.612768     1531      0.603469  
3       0.460804     2358      0.471883     1181      0.465510  
4       0.112614      561      0.112267      279      0.109972

Voy a crear una función que me permita agilizar el proceso de comparar los tres grupos en cada conjunto de datos (Número de Eventos)

## **Función de comparación**

In [44]:
# Función para comparar las pruebas

def analizar_eventos_aa_b(df, alpha=0.05):
    """
    Compara la proporción de usuarios que realizaron eventos entre los grupos A1 y A2
    Utiliza la prueba de chi-cuadrado de independencia con corrección de Bonferroni.

    Parámetros:
    - df: DataFrame con columnas 'event' y 'group' (A1, A2, B).
    - alpha: Nivel de significancia antes de la corrección (default 0.05).

    Retorna:
    - Resultados de la prueba estadística para cada evento y comparación.
    """

    # Obtener los eventos únicos
    eventos_unicos = ['Tutorial', 'Main Screen Appear', 'Offers Screen Appear',
       'Cart Screen Appear', 'Payment Screen Successful']
    
    # Aplicar la corrección de Bonferroni (para todas las comparaciones posibles)
    
    alpha_bonferroni = alpha

    # Definir las comparaciones entre los grupos
    comparaciones = [('A1', 'A2')]

    for evento in eventos_unicos:
        print(f"\n📊 Comparando el evento: {evento}")

        # Filtrar los datos por evento específico
        df_evento = df[df['event'] == evento]

        # Contar el número de usuarios por grupo para ese evento
        conteo_usuarios = df_evento['group'].value_counts()

        for group1, group2 in comparaciones:
            # Obtener las cuentas para cada grupo, si no existen asignar 0
            count_group1 = conteo_usuarios.get(group1, 0)
            count_group2 = conteo_usuarios.get(group2, 0)

            # Crear la tabla de contingencia
            tabla = pd.DataFrame({
                group1: [count_group1, len(df[df['group'] == group1]) - count_group1],
                group2: [count_group2, len(df[df['group'] == group2]) - count_group2]
            }, index=['Realizó evento', 'No realizó evento'])

            # Aplicar la prueba de chi-cuadrado
            chi2_stat, p_valor, _, _ = chi2_contingency(tabla)

            print(f"\nComparación {group1} vs {group2}:")
            print(f"  - P-valor: {p_valor:.4f}")

            if p_valor < alpha_bonferroni:
                print(f"  🔴 Diferencia estadísticamente significativa entre {group1} y {group2} ❗")
            else:
                print(f"  🟢 No hay diferencia estadísticamente significativa entre {group1} y {group2} ✅")


**Comparaciones de los eventos de A1 y A2 utilizando la función**

In [45]:
analizar_eventos_aa_b(df_agosto)


📊 Comparando el evento: Tutorial

Comparación A1 vs A2:
  - P-valor: 0.2472
  🟢 No hay diferencia estadísticamente significativa entre A1 y A2 ✅

📊 Comparando el evento: Main Screen Appear

Comparación A1 vs A2:
  - P-valor: 0.0000
  🔴 Diferencia estadísticamente significativa entre A1 y A2 ❗

📊 Comparando el evento: Offers Screen Appear

Comparación A1 vs A2:
  - P-valor: 0.0000
  🔴 Diferencia estadísticamente significativa entre A1 y A2 ❗

📊 Comparando el evento: Cart Screen Appear

Comparación A1 vs A2:
  - P-valor: 0.0000
  🔴 Diferencia estadísticamente significativa entre A1 y A2 ❗

📊 Comparando el evento: Payment Screen Successful

Comparación A1 vs A2:
  - P-valor: 0.0000
  🔴 Diferencia estadísticamente significativa entre A1 y A2 ❗


La prueba sugiere que los grupos de control (A1 y A2) son diferentes en la mayoría de los eventos, tan solo en el tutorial no hubo diferencia estadística.

**Comparación entre A y B**

Ahora voy a sumar a los usuarios del grupo A1 y A2 para compararlos contra los usuarios del grupo B

In [46]:
# Obtener los eventos únicos
eventos_unicos = ['Tutorial', 'Main Screen Appear', 'Offers Screen Appear',
       'Cart Screen Appear', 'Payment Screen Successful']

# Nivel de significancia y corrección de Bonferroni
alpha = 0.05
alpha_bonferroni = alpha

print(f"Comparación Grupos Control (A1 + A2) vs B:")

for evento in eventos_unicos:
    print(f"\n📊 Comparando el evento: {evento}")

    # Filtrar datos del evento actual
    df_evento = df_agosto[df_agosto['event'] == evento]

    # Contar usuarios en cada grupo
    count_A1 = df_evento[df_evento['group'] == 'A1'].shape[0]
    count_A2 = df_evento[df_evento['group'] == 'A2'].shape[0]
    count_B = df_evento[df_evento['group'] == 'B'].shape[0]

    # Sumar A1 y A2 para combinar los grupos de control
    count_control = count_A1 + count_A2
    total_control = df_agosto[df_agosto['group'].isin(['A1', 'A2'])].shape[0] - count_control
    total_B = df_agosto[df_agosto['group'] == 'B'].shape[0] - count_B

    # Crear la tabla de contingencia para la prueba de chi-cuadrado
    tabla = pd.DataFrame({
        'Control (A1 + A2)': [count_control, total_control],
        'B': [count_B, total_B]
    }, index=['Realizó evento', 'No realizó evento'])

    # Aplicar la prueba de chi-cuadrado
    chi2_stat, p_valor, _, _ = chi2_contingency(tabla)


    print(f"  - Estadístico Chi-cuadrado: {chi2_stat:.4f}")
    print(f"  - P-valor: {p_valor:.4f}")
    print(f"  - Alpha con Bonferroni: {alpha_bonferroni:.4f}")

    if p_valor < alpha_bonferroni:
        print(f"  🔴 Diferencia estadísticamente significativa entre Control y B ❗")
    else:
        print(f"  🟢 No hay diferencia estadísticamente significativa entre Control y B ✅")

Comparación Grupos Control (A1 + A2) vs B:

📊 Comparando el evento: Tutorial
  - Estadístico Chi-cuadrado: 0.0233
  - P-valor: 0.8787
  - Alpha con Bonferroni: 0.0500
  🟢 No hay diferencia estadísticamente significativa entre Control y B ✅

📊 Comparando el evento: Main Screen Appear
  - Estadístico Chi-cuadrado: 28.5198
  - P-valor: 0.0000
  - Alpha con Bonferroni: 0.0500
  🔴 Diferencia estadísticamente significativa entre Control y B ❗

📊 Comparando el evento: Offers Screen Appear
  - Estadístico Chi-cuadrado: 1.7280
  - P-valor: 0.1887
  - Alpha con Bonferroni: 0.0500
  🟢 No hay diferencia estadísticamente significativa entre Control y B ✅

📊 Comparando el evento: Cart Screen Appear
  - Estadístico Chi-cuadrado: 13.5496
  - P-valor: 0.0002
  - Alpha con Bonferroni: 0.0500
  🔴 Diferencia estadísticamente significativa entre Control y B ❗

📊 Comparando el evento: Payment Screen Successful
  - Estadístico Chi-cuadrado: 4.7531
  - P-valor: 0.0292
  - Alpha con Bonferroni: 0.0500
  🔴 Dife

<div class="alert alert-block alert-warning">
<b>Comentario de Revisor</b> <a class="tocSkip"></a>
Cuidado!<br/>

En esta última parte no es lo mejor combinar ambos grupos de control, cada uno de ellos debe tratarse de forma separada, esta es la razón principal de hacer una prueba A/A/B, la de tener dos puntos de comparación independientes, al combinarl
 
</div>

## **Conclusión**

No hay evidencia para concluir que B sea mejor que el grupo de control (A1 y A2), más bien parece ser inferior según la proporción que obtuvimos en los resultados de cada evento. Por lo tanto concluyo que el grupo B tiene peores resultados, rechazo la hipótesis de que el grupo B sea mejor.

# Comentario general del revisor
<div class="alert alert-block alert-success">
<b>Comentario del revisor</b> <a class="tocSkip"></a><br />
Has realizado un buen trabajo, me doy cuenta de que has aplicado los conocimientos que has adquirido durante el curso, los procedimientos realizados son correctos.<br/>
 
Las decisiones que tomas a lo largo del proyecto me parecen acertadas y te hacen ir por un buen camino, lo que termina en un analisis bastante acertado.    
<br/>
Las conclusiones finales a las que llegas estan respaldadas con los procedimientos que has realizado a lo largo del proyecto, me parecen bastante acertadas y el lenguaje que usas es adecuado para que cualquier persona las pueda entender.
<br/> <br/> 

    
    
Este tipo de analisis ayudará al negocio a enfocarse en partes especificas de los distintos eventos que los usuarios toman para llegar a realizar una compra, en este caso se pueden enfocar en la parte donde se pierden la mayoría de usuarios que es el pasar de la pantalla principal a la pantalla de ofertas. Se pueden crear distintas maneras de generar mas enganche para que cada vez más personas pasen de una etapa a la siguiente.<br/>
Continúa con el buen trabajo y mucho éxito en el siguiente Sprint!
</div>


**Correcciones**

In [48]:
ids = df_agosto[['device_id', 'group']].drop_duplicates()
ids

device_id group
2828    3737462046622621720    A1
2832    1433840883824088890    A2
2833    4899590676214355127    A2
2840    1182179323890311443    A1
2844    4613461174774205834     B
...                     ...   ...
243339  5811573131275421338     B
243542  5365227480683749189     B
243777  6660805781687343085    A1
243820  7823752606740475984    A1
243862  3454683894921357834    A2

[7534 rows x 2 columns]

In [67]:
tutorial = df_agosto[df_agosto['event'] == 'Tutorial'][['device_id', 'group']].drop_duplicates()
tutorial['tutorial'] = 1
tutorial

device_id group  tutorial
2828    3737462046622621720    A1         1
3353    5587388800188073787    A2         1
3433    2988069914968447512    A1         1
3590    1884616937397676465    A2         1
3622    5422877498318042547    A1         1
...                     ...   ...       ...
241781  1309234519709630135    A2         1
241869  5523029501947287934    A2         1
242673  4069063897900929368     B         1
242695  5862484110925354625    A2         1
243542  5365227480683749189     B         1

[840 rows x 3 columns]

In [68]:
Payment_Screen_Successful = df_agosto[df_agosto['event'] == 'Payment Screen Successful'][['device_id', 'group']].drop_duplicates()
Payment_Screen_Successful['Payment Screen Successful'] = 1
Payment_Screen_Successful

device_id group  Payment Screen Successful
2847    4613461174774205834     B                          1
2863    2712290788139738557    A2                          1
2913    6049698452889664846    A2                          1
2992    5653442602434498252    A1                          1
3037    6126676435667432321    A1                          1
...                     ...   ...                        ...
241297  4369662623769092250     B                          1
241480  4876403292056911122    A1                          1
242317  1309234519709630135    A2                          1
243822  7823752606740475984    A1                          1
243828  4164287718073415198    A1                          1

[3539 rows x 3 columns]

In [69]:
Cart_Screen_Appear = df_agosto[df_agosto['event'] == 'Cart Screen Appear'][['device_id', 'group']].drop_duplicates()
Cart_Screen_Appear['Cart Screen Appear'] = 1
Cart_Screen_Appear

device_id group  Cart Screen Appear
2846    4613461174774205834     B                   1
2864    2712290788139738557    A2                   1
2912    6049698452889664846    A2                   1
2993    5653442602434498252    A1                   1
3036    6126676435667432321    A1                   1
...                     ...   ...                 ...
242081  5208270606211794573     B                   1
243707  2457909310456664267    A2                   1
243823  7823752606740475984    A1                   1
243829  4164287718073415198    A1                   1
243873  3454683894921357834    A2                   1

[3734 rows x 3 columns]

In [70]:
Offers_Screen_Appear = df_agosto[df_agosto['event'] == 'Offers Screen Appear'][['device_id', 'group']].drop_duplicates()
Offers_Screen_Appear['Offers Screen Appear'] = 1
Offers_Screen_Appear

device_id group  Offers Screen Appear
2831    3737462046622621720    A1                     1
2839    4899590676214355127    A2                     1
2848    4613461174774205834     B                     1
2853    6121366368901703338     B                     1
2857    6022375714473447159     B                     1
...                     ...   ...                   ...
243727  6400775428226321371    A2                     1
243753   165544483717321054     B                     1
243809  4164287718073415198    A1                     1
243825  7823752606740475984    A1                     1
244074  3014810502934076967    A2                     1

[4593 rows x 3 columns]

In [71]:
Main_Screen_Appear = df_agosto[df_agosto['event'] == 'Main Screen Appear'][['device_id', 'group']].drop_duplicates()
Main_Screen_Appear['Main Screen Appear'] = 1
Main_Screen_Appear

device_id group  Main Screen Appear
2829    3737462046622621720    A1                   1
2832    1433840883824088890    A2                   1
2833    4899590676214355127    A2                   1
2840    1182179323890311443    A1                   1
2844    4613461174774205834     B                   1
...                     ...   ...                 ...
243339  5811573131275421338     B                   1
243544  5365227480683749189     B                   1
243777  6660805781687343085    A1                   1
243820  7823752606740475984    A1                   1
243862  3454683894921357834    A2                   1

[7419 rows x 3 columns]

In [77]:
ids_merged = ids.merge(Main_Screen_Appear, on=['device_id', 'group'], how='left')
ids_merged = ids_merged.merge(Offers_Screen_Appear, on=['device_id', 'group'], how='left')
ids_merged = ids_merged.merge(Cart_Screen_Appear, on=['device_id', 'group'], how='left')
ids_merged = ids_merged.merge(Payment_Screen_Successful, on=['device_id', 'group'], how='left')
ids_merged = ids_merged.merge(tutorial, on=['device_id', 'group'], how='left')
ids_merged = ids_merged.fillna(0)

In [78]:
ids_merged

device_id group  Main Screen Appear  Offers Screen Appear  \
0     3737462046622621720    A1                 1.0                   1.0   
1     1433840883824088890    A2                 1.0                   0.0   
2     4899590676214355127    A2                 1.0                   1.0   
3     1182179323890311443    A1                 1.0                   0.0   
4     4613461174774205834     B                 1.0                   1.0   
...                   ...   ...                 ...                   ...   
7529  5811573131275421338     B                 1.0                   0.0   
7530  5365227480683749189     B                 1.0                   0.0   
7531  6660805781687343085    A1                 1.0                   0.0   
7532  7823752606740475984    A1                 1.0                   1.0   
7533  3454683894921357834    A2                 1.0                   0.0   

      Cart Screen Appear  Payment Screen Successful  tutorial  
0                    1.0                        1.0       1.0  
1                    0.0                        0.0       0.0  
2                    1.0                        1.0       0.0  
3                    0.0                        0.0       0.0  
4                    1.0                        1.0       0.0  
...                  ...                        ...       ...  
7529                 0.0                        0.0       0.0  
7530                 0.0                        0.0       1.0  
7531                 0.0                        0.0       0.0  
7532                 1.0                        1.0       0.0  
7533                 1.0                        0.0       0.0  

[7534 rows x 7 columns]

In [79]:
ids_merged['Main Screen Appear'].mean()

0.9847358640828245

In [86]:
a1 = ids_merged[ids_merged['group'] == 'A1']

In [87]:
a2 = ids_merged[ids_merged['group'] == 'A2']

In [88]:
b = ids_merged[ids_merged['group'] == 'B']

In [ ]:
ttest_ind(
    a1['Main Screen Appear'], 
    b['Main Screen Appear'])

TtestResult(statistic=1.0471820148439275, pvalue=0.29506606465679125, df=5019.0)

Parámetros necesarios para construir una prueba T (Student)

- Medias a comparar.
- Las varianzas.
- Número de observaciones.

In [ ]:
# Nivel crítico de significación estadística
alpha = .05

# Prueba la hipótesis de que las medias de las dos poblaciones independientes son iguales
results = ttest_ind(pages_per_session_autumn, pages_per_session_summer, equal_var=False)

# Imprimir el valor p obtenido
print('valor p:',results.pvalue)

# Comparar los valores p obtenidos con el nivel de significación estadística)
if results.pvalue < alpha:
    print("Rechazamos la hipótesis nula")
else:
    print("No podemos rechazar la hipótesis nula")